In [4]:
import pandas as pd

In [5]:
# Load a CSV file into a pandas dataframe
df = pd.read_csv('train_labels.csv')

# Display the first few rows of the dataframe
print(df.head())

                brand       brandtext category     type  size  \
0            Dressman             NaN      Men  T-shirt  XXXL   
1  Amisu (New Yorker)             NaN   Ladies  T-shirt     L   
2     Not in the list     FRANK LYMAN   Ladies    Dress    40   
3     Not in the list  Shirt Industry      Men    Shirt     L   
4             Kappahl             NaN   Ladies      Top    XL   

                                     colors  season  pilling  condition  \
0                ['Grey', 'Blue', 'Yellow']     All        3          3   
1                                  ['Pink']     All        5          3   
2  ['Black', 'Pink', 'Green', 'Multicolor']     All        5          5   
3                       ['Purple', 'White']  Spring        4          3   
4                                  ['Grey']     All        4          2   

    price  ... styleholes damageimage damageloc damage2image damage2loc  \
0     <50  ...        NaN         NaN       NaN          NaN        NaN   
1     <5

/var/folders/vm/f0xl736s0451sjjq26sll95w0000gn/T/ipykernel_23600/1631229452.py:2: DtypeWarning: Columns (10) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('train_labels.csv')


In [ ]:
import torch
import torch.nn as nn
import torchvision.models as models

class CustomResNet(nn.Module):
    def __init__(self, input_channels=3, num_classes=1000):
        super(CustomResNet, self).__init__()
        self.resnet = models.resnet50(pretrained=True)
        
        # Modify the first convolutional layer to accept the desired input size
        self.resnet.conv1 = nn.Conv2d(input_channels, 64, kernel_size=7, stride=2, padding=3, bias=False)
        
        # Modify the final fully connected layer to match the number of classes
        self.resnet.fc = nn.Linear(self.resnet.fc.in_features, num_classes)
    
    def forward(self, x):
        return self.resnet(x)

# Example usage
model = CustomResNet(input_channels=3, num_classes=5)  # For grayscale images and 10 classes
print(model)

/Users/adamtsou/clothingquality/clothing/lib/python3.8/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/Users/adamtsou/clothingquality/clothing/lib/python3.8/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
Downloading: "https://download.pytorch.org/models/resnet50-0676ba61.pth" to /Users/adamtsou/.cache/torch/hub/checkpoints/resnet50-0676ba61.pth
100%|██████████| 97.8M/97.8M [00:04<00:00, 24.4MB/s]


CustomResNet(
  (resnet): ResNet(
    (conv1): Conv2d(1, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
    (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (relu): ReLU(inplace=True)
    (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
    (layer1): Sequential(
      (0): Bottleneck(
        (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
        (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
        (bn3): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (relu): ReLU(inplace=True)
        (downsample): Sequential(
      

In [ ]:
import torch
import torch.nn as nn
import torch.optim as optim
from torchvision import datasets, transforms, models
from torch.utils.data import DataLoader

# Define the custom ResNet model
class CustomResNet(nn.Module):
    def __init__(self, input_channels=3, num_classes=5):
        super(CustomResNet, self).__init__()
        self.resnet = models.resnet50(pretrained=True)
        
        # Modify the first convolutional layer to accept the desired input size
        self.resnet.conv1 = nn.Conv2d(input_channels, 64, kernel_size=7, stride=2, padding=3, bias=False)
        
        # Modify the final fully connected layer to match the number of classes
        self.resnet.fc = nn.Linear(self.resnet.fc.in_features, num_classes)
    
    def forward(self, x):
        return self.resnet(x)

# Define transformations for the training and validation sets
transform = transforms.Compose([
    transforms.Resize((180, 640)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

# Load the dataset
train_dataset = datasets.ImageFolder(root='/Users/adamtsou/clothingquality/fused', transform=transform)
train_dataset = 
# Create a data loader
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True)

# Initialize the model, loss function, and optimizer
model = CustomResNet(input_channels=3, num_classes=5)
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)

# Training loop
num_epochs = 10
device = torch.device('cuda' if torch.cuda.is_available() else 'mps' else 'cpu')
model.to(device)

for epoch in range(num_epochs):
    model.train()
    running_loss = 0.0
    for inputs, labels in train_loader:
        inputs, labels = inputs.to(device), labels.to(device)
        
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()
        
        running_loss += loss.item() * inputs.size(0)
    
    epoch_loss = running_loss / len(train_loader.dataset)
    print(f'Epoch {epoch+1}/{num_epochs}, Loss: {epoch_loss:.4f}')

print("Training complete.")

In [7]:
import os

# Directory containing the files
directory = '/Users/adamtsou/clothingquality/fused'

# Iterate over all files in the directory
for filename in os.listdir(directory):
    if filename.endswith('.jpg_fused.jpg'):
        # Create the new filename
        new_filename = filename.replace('.jpg_fused.jpg', '.jpg')
        
        # Get the full paths
        old_file = os.path.join(directory, filename)
        new_file = os.path.join(directory, new_filename)
        
        # Rename the file
        os.rename(old_file, new_file)
        print(f'Renamed: {old_file} -> {new_file}')

print("Renaming complete.")

Renamed: /Users/adamtsou/clothingquality/fused/2023_09_11_09_23_22.jpg_fused.jpg -> /Users/adamtsou/clothingquality/fused/2023_09_11_09_23_22.jpg
Renamed: /Users/adamtsou/clothingquality/fused/2023_09_26_13_29_46.jpg_fused.jpg -> /Users/adamtsou/clothingquality/fused/2023_09_26_13_29_46.jpg
Renamed: /Users/adamtsou/clothingquality/fused/2023_04_14_05_56_06.jpg_fused.jpg -> /Users/adamtsou/clothingquality/fused/2023_04_14_05_56_06.jpg
Renamed: /Users/adamtsou/clothingquality/fused/2024_02_02_08_52_39.jpg_fused.jpg -> /Users/adamtsou/clothingquality/fused/2024_02_02_08_52_39.jpg
Renamed: /Users/adamtsou/clothingquality/fused/2024_01_31_07_29_06.jpg_fused.jpg -> /Users/adamtsou/clothingquality/fused/2024_01_31_07_29_06.jpg
Renamed: /Users/adamtsou/clothingquality/fused/2023_10_20_09_26_34.jpg_fused.jpg -> /Users/adamtsou/clothingquality/fused/2023_10_20_09_26_34.jpg
Renamed: /Users/adamtsou/clothingquality/fused/2023_07_14_07_01_55.jpg_fused.jpg -> /Users/adamtsou/clothingquality/fused/20